In [1]:
import os
import pandas as pd
from imblearn.over_sampling import SMOTE
import numpy as np

'''
Split the dataset: Divide the data into training, validation, and test sets.
Apply SMOTE: Apply SMOTE only to the training set to balance the class distribution.
Train the model: Train your machine learning model on the balanced training set.
Evaluate the model: Use the untouched validation and test sets to assess the model's performance.

'''

'''
1. Use the SMOTE.py code instead of this one
2. The use the validate_sample.py to get the invalid samples
3. Then get the list from the log.out and use the last code segment to exclude it from the list
4. You are all set to train the model
'''

'\n1. Use the SMOTE.py code instead of this one\n2. The use the validate_sample.py to get the invalid samples\n3. Then get the list from the log.out and use the last code segment to exclude it from the list\n4. You are all set to train the model\n'

In [2]:
%pwd
%cd '/raid/home/tanmoysarkar/Trustworthiness/MIMIC-III/mimic3-benchmarks'

/raid/home/tanmoysarkar/Trustworthiness/MIMIC-III/mimic3-benchmarks


## Set GCS options

In [3]:
GCS_motor =  {
"1 No Response": 1,
"No response": 1,
"2 Abnorm extensn": 2,
"Abnormal extension": 2,
"3 Abnorm flexion": 3,
"Abnormal Flexion": 3,
"4 Flex-withdraws": 4,
"Flex-withdraws": 4,
"5 Localizes Pain": 5,
"Localizes Pain": 5,
"6 Obeys Commands": 6,
"Obeys Commands": 6
}


GCS_motor_reverse =  {
1: "1 No Response",
2: "2 Abnorm extensn",
3: "3 Abnorm flexion",
4: "4 Flex-withdraws",
5: "5 Localizes Pain",
6: "6 Obeys Commands",
}



GCS_eye = {
"None": 0,
"1 No Response": 1,
"2 To pain": 2,
"To Pain": 2,
"3 To speech": 3,
"To Speech": 3,
"4 Spontaneously": 4,
"Spontaneously": 4
}


GCS_eye_reverse = {
0: "None",
1: "1 No Response",
2: "2 To pain",
3: "3 To speech",
4: "4 Spontaneously",
}


GCS_speech = {
"No Response-ETT": 1,
"No Response": 1,
"1 No Response": 1,
"1.0 ET/Trach": 1,
"2 Incomp sounds": 2,
"Incomprehensible sounds": 2,
"3 Inapprop words": 3,
"Inappropriate Words": 3,
"4 Confused": 4,
"Confused": 4,
"5 Oriented": 5,
"Oriented": 5
}


GCS_speech_reverse = {
1: "1 No Response",
2: "2 Incomp sounds",
3: "3 Inapprop words",
4: "4 Confused",
5: "5 Oriented",
}


# # Load the data from the CSV file

# df['Glascow coma scale eye opening'] = df['Glascow coma scale eye opening'].map(GCS_eye)
# df['Glascow coma scale motor response'] = df['Glascow coma scale motor response'].map(GCS_motor)
# df['Glascow coma scale verbal response'] = df['Glascow coma scale verbal response'].map(GCS_speech)
# df['Glascow coma scale total'] = df['Glascow coma scale total'].astype('Int64')

# MIMIC III

## Flat dataset

In [20]:
s = "train"
# Define paths
data_folder = 'data/task-data/in-hospital-mortality/train-filled-48H'
label_file = 'data/task-data/in-hospital-mortality/train_listfile.csv'
output_folder = 'data/task-data/in-hospital-mortality/train-filled-48H-SMOTE'
output_folder_labels = "data/task-data/in-hospital-mortality/"


# Create the output directory if it doesn't exist
os.makedirs(output_folder, exist_ok=True)

# Load the labels
labels_df = pd.read_csv(label_file)
display(labels_df)

# Initialize lists to store data points and labels
data_list = []
label_list = []

counter = 1

# Iterate through each file and prepare data
for index, row in labels_df.iterrows():
    file_name = row['stay']
    label = row['y_true']  # Assuming the label column is named 'y_true'
    
    # Load the CSV file
    file_path = os.path.join(data_folder, file_name)
    df = pd.read_csv(file_path)

    df['Glascow coma scale eye opening'] = df['Glascow coma scale eye opening'].map(GCS_eye)
    df['Glascow coma scale motor response'] = df['Glascow coma scale motor response'].map(GCS_motor)
    df['Glascow coma scale verbal response'] = df['Glascow coma scale verbal response'].map(GCS_speech)
    df['Glascow coma scale total'] = df['Glascow coma scale total'].astype('Int64')
    df['Hours'] = df["Hours"].astype(float)
    
    # Flatten the 2D data into 1D
    data_flattened = df.values.flatten()
    
    # Add to the lists
    data_list.append(data_flattened)
    label_list.append(label)

    print(counter, file_name, label, df.shape, data_flattened.shape)
    counter += 1

# Convert to numpy arrays
X = np.array(data_list)
y = np.array(label_list)

print(X.shape, y.shape)

np.save(output_folder_labels + "X_" + s + "_filled_48H_flattened_raw.npy", X)
np.save(output_folder_labels + "y_" + s + "_filled_48H_flattened_raw.npy", y)


stay  y_true
0      68251_episode2_timeseries.csv       0
1      82293_episode1_timeseries.csv       0
2       3011_episode1_timeseries.csv       0
3      52021_episode1_timeseries.csv       0
4      64371_episode1_timeseries.csv       0
...                              ...     ...
14676  27212_episode1_timeseries.csv       1
14677  97488_episode2_timeseries.csv       1
14678  26607_episode1_timeseries.csv       0
14679  14467_episode3_timeseries.csv       0
14680   6598_episode3_timeseries.csv       0

[14681 rows x 2 columns]

1 68251_episode2_timeseries.csv 0 (49, 18) (882,)
2 82293_episode1_timeseries.csv 0 (49, 18) (882,)
3 3011_episode1_timeseries.csv 0 (49, 18) (882,)
4 52021_episode1_timeseries.csv 0 (49, 18) (882,)
5 64371_episode1_timeseries.csv 0 (49, 18) (882,)
6 29861_episode3_timeseries.csv 0 (49, 18) (882,)
7 3794_episode1_timeseries.csv 1 (49, 18) (882,)
8 26754_episode2_timeseries.csv 0 (49, 18) (882,)
9 32156_episode1_timeseries.csv 0 (49, 18) (882,)
10 3133_episode1_timeseries.csv 1 (49, 18) (882,)
11 81848_episode1_timeseries.csv 0 (49, 18) (882,)
12 2151_episode1_timeseries.csv 0 (49, 18) (882,)
13 4738_episode1_timeseries.csv 0 (49, 18) (882,)
14 15504_episode1_timeseries.csv 1 (49, 18) (882,)
15 19996_episode1_timeseries.csv 0 (49, 18) (882,)
16 7656_episode1_timeseries.csv 0 (49, 18) (882,)
17 52172_episode2_timeseries.csv 0 (49, 18) (882,)
18 919_episode1_timeseries.csv 0 (49, 18) (882,)
19 65906_episode1_timeseries.csv 0 (49, 18) (882,)
20 16947_episode1_timeseries.csv 0 (49, 18) (882

## Apply SMOTE and Save as csv files

In [ ]:
s = "train"
# Define paths
data_folder = 'data/task-data/in-hospital-mortality/train-filled-48H'
label_file = 'data/task-data/in-hospital-mortality/train_listfile.csv'
output_folder = 'data/task-data/in-hospital-mortality/train-filled-48H-SMOTE'
output_folder_labels = "data/task-data/in-hospital-mortality/"

default_values = {
    "Capillary refill rate": "0.0",
    "Diastolic blood pressure": "59.0",
    "Fraction inspired oxygen": "0.21",
    "Glascow coma scale eye opening": "4 Spontaneously",
    "Glascow coma scale motor response": "6 Obeys Commands",
    "Glascow coma scale total": "15",
    "Glascow coma scale verbal response": "5 Oriented",
    "Glucose": "128.0",
    "Heart Rate": "86",
    "Height": "170.0",
    "Mean blood pressure": "77.0",
    "Oxygen saturation": "98.0",
    "Respiratory rate": "19",
    "Systolic blood pressure": "118.0",
    "Temperature": "36.6",
    "Weight": "81.0",
    "pH": "7.4"
  }

# Create the output directory if it doesn't exist
os.makedirs(output_folder, exist_ok=True)

import numpy as np
# save np.load
np_load_old = np.load

# modify the default parameters of np.load
np.load = lambda *a,**k: np_load_old(*a, allow_pickle=True, **k)

X = np.load(output_folder_labels + "X_" + s + "_filled_48H_flattened_raw.npy")
y = np.load(output_folder_labels + "y_" + s + "_filled_48H_flattened_raw.npy")

# restore np.load for future normal usage
np.load = np_load_old

print("SMOTE Working ......")
# Apply SMOTE
smote = SMOTE(sampling_strategy='auto', random_state=42)
X_resampled, y_resampled = smote.fit_resample(X, y)

print("SMOTE Completed!!")

missing = []
c = 1

# Iterate through the resampled data and save them as new CSV files
for i, (data_row, label) in enumerate(zip(X_resampled, y_resampled)):
    # Reshape back to the original 2D format (number of rows and columns)
    reshaped_data = data_row.reshape(df.shape)
    
    # Convert to DataFrame
    resampled_df = pd.DataFrame(reshaped_data, columns=df.columns)

    if resampled_df.isnull().values.any():
        print("Missing:" , c)
        c += 1

    resampled_df['Glascow coma scale eye opening'] = resampled_df['Glascow coma scale eye opening'].map(GCS_eye_reverse)
    resampled_df['Glascow coma scale motor response'] = resampled_df['Glascow coma scale motor response'].map(GCS_motor_reverse)
    resampled_df['Glascow coma scale verbal response'] = resampled_df['Glascow coma scale verbal response'].map(GCS_speech_reverse)

    resampled_df = resampled_df.fillna(method='ffill')  # Fill missing values with previous row values
    resampled_df = resampled_df.fillna(default_values)  # Fill remaining missing values with default values

    resampled_df['Glascow coma scale total'] = resampled_df['Glascow coma scale total'].round()
    resampled_df['Glascow coma scale total'] = resampled_df['Glascow coma scale total'].astype('Int64')
    resampled_df['Hours'] = resampled_df["Hours"].astype(float)
    
    # Generate a new file name
    new_file_name = f'resampled_{i}.csv'
    new_file_path = os.path.join(output_folder, new_file_name)
    
    # Save the DataFrame as CSV
    resampled_df.to_csv(new_file_path, index=False)
    
    print(i, new_file_name)
    if resampled_df.isnull().values.any():
        missing.append(new_file_name)

 
# Save the new labels
resampled_labels_df = pd.DataFrame({
    'stay': [f'resampled_{i}.csv' for i in range(len(y_resampled))],
    'y_true': y_resampled
})

resampled_labels_file = os.path.join(output_folder_labels, s+'_val_SMOTE_labels.csv')
resampled_labels_df.to_csv(resampled_labels_file, index=False)

print(f"Saved resampled labels to: {resampled_labels_file}")
print(len(missing), missing)

In [29]:
print("Train set class distribution:\n", resampled_labels_df['y_true'].value_counts(normalize=True))

Train set class distribution:
 1    0.5
0    0.5
Name: y_true, dtype: float64


In [23]:
test_SMOTE_list = pd.read_csv("data/task-data/in-hospital-mortality/test_SMOTE_labels.csv")

print("Train set class distribution:\n", test_SMOTE_list['y_true'].value_counts(normalize=True))

Train set class distribution:
 1    0.5
0    0.5
Name: y_true, dtype: float64


In [11]:
import pandas as pd
import os

def find_missing_values(data_dir):
  missing_files = []

  c = 0

  for filename in os.listdir(data_dir):
    print(c, filename)
    c += 1
    if filename.endswith('.csv'):
      file_path = os.path.join(data_dir, filename)
      df = pd.read_csv(file_path)
      if df.isnull().values.any():
        missing_files.append(filename)
        print("XXXX", filename)

  return missing_files

# Example usage
data_dir = 'data/task-data/in-hospital-mortality/train-filled-48H-SMOTE'
folder_path = 'data/task-data/in-hospital-mortality/train-filled-48H-SMOTE'
missing_files = find_missing_values(data_dir)
print(missing_files)


0 resampled_0.csv
1 resampled_1.csv
2 resampled_2.csv
3 resampled_3.csv
4 resampled_4.csv
5 resampled_5.csv
6 resampled_6.csv
7 resampled_7.csv
8 resampled_8.csv
9 resampled_9.csv
10 resampled_10.csv
11 resampled_11.csv
12 resampled_12.csv
13 resampled_13.csv
14 resampled_14.csv
15 resampled_15.csv
16 resampled_16.csv
17 resampled_17.csv
18 resampled_18.csv
19 resampled_19.csv
20 resampled_20.csv
21 resampled_21.csv
22 resampled_22.csv
23 resampled_23.csv
24 resampled_24.csv
25 resampled_25.csv
26 resampled_26.csv
27 resampled_27.csv
28 resampled_28.csv
29 resampled_29.csv
30 resampled_30.csv
31 resampled_31.csv
32 resampled_32.csv
33 resampled_33.csv
34 resampled_34.csv
35 resampled_35.csv
36 resampled_36.csv
37 resampled_37.csv
38 resampled_38.csv
39 resampled_39.csv
40 resampled_40.csv
41 resampled_41.csv
42 resampled_42.csv
43 resampled_43.csv
44 resampled_44.csv
45 resampled_45.csv
46 resampled_46.csv
47 resampled_47.csv
48 resampled_48.csv
49 resampled_49.csv
50 resampled_50.csv


## Remove the invalid samples from the data list

In [8]:
Invalid_files =  ['resampled_14792.csv', 'resampled_14808.csv', 'resampled_14890.csv', 'resampled_15019.csv', 'resampled_15197.csv', 'resampled_15200.csv', 'resampled_15359.csv', 'resampled_15374.csv', 'resampled_15524.csv', 'resampled_15532.csv', 'resampled_15593.csv', 'resampled_15693.csv', 'resampled_15730.csv', 'resampled_15779.csv', 'resampled_15869.csv', 'resampled_16040.csv', 'resampled_16089.csv', 'resampled_16101.csv', 'resampled_16227.csv', 'resampled_16302.csv', 'resampled_16317.csv', 'resampled_16424.csv', 'resampled_16707.csv', 'resampled_16755.csv', 'resampled_16824.csv', 'resampled_16870.csv', 'resampled_16933.csv', 'resampled_16986.csv', 'resampled_17028.csv', 'resampled_17043.csv', 'resampled_17060.csv', 'resampled_17080.csv', 'resampled_17090.csv', 'resampled_17108.csv', 'resampled_17142.csv', 'resampled_17156.csv', 'resampled_17199.csv', 'resampled_17293.csv', 'resampled_17377.csv', 'resampled_17394.csv', 'resampled_17457.csv', 'resampled_17459.csv', 'resampled_17479.csv', 'resampled_17868.csv', 'resampled_17927.csv', 'resampled_17965.csv', 'resampled_18033.csv', 'resampled_18137.csv', 'resampled_18250.csv', 'resampled_18280.csv', 'resampled_18287.csv', 'resampled_18377.csv', 'resampled_18540.csv', 'resampled_18601.csv', 'resampled_18637.csv', 'resampled_18639.csv', 'resampled_18687.csv', 'resampled_18732.csv', 'resampled_18775.csv', 'resampled_18794.csv', 'resampled_18814.csv', 'resampled_18825.csv', 'resampled_18828.csv', 'resampled_18996.csv', 'resampled_19021.csv', 'resampled_19031.csv', 'resampled_19438.csv', 'resampled_19602.csv', 'resampled_19610.csv', 'resampled_19758.csv', 'resampled_19832.csv', 'resampled_19837.csv', 'resampled_20009.csv', 'resampled_20023.csv', 'resampled_20057.csv', 'resampled_20153.csv', 'resampled_20268.csv', 'resampled_20307.csv', 'resampled_20353.csv', 'resampled_20356.csv', 'resampled_20446.csv', 'resampled_20502.csv', 'resampled_20521.csv', 'resampled_20557.csv', 'resampled_20780.csv', 'resampled_20805.csv', 'resampled_20842.csv', 'resampled_21019.csv', 'resampled_21062.csv', 'resampled_21178.csv', 'resampled_21353.csv', 'resampled_21405.csv', 'resampled_21431.csv', 'resampled_21456.csv', 'resampled_21468.csv', 'resampled_21472.csv', 'resampled_21528.csv', 'resampled_21714.csv', 'resampled_21721.csv', 'resampled_21743.csv', 'resampled_21832.csv', 'resampled_21905.csv', 'resampled_21916.csv', 'resampled_21957.csv', 'resampled_22045.csv', 'resampled_22090.csv', 'resampled_22200.csv', 'resampled_22217.csv', 'resampled_22232.csv', 'resampled_22279.csv', 'resampled_22325.csv', 'resampled_22366.csv', 'resampled_22448.csv', 'resampled_22453.csv', 'resampled_22515.csv', 'resampled_22581.csv', 'resampled_22608.csv', 'resampled_22661.csv', 'resampled_22798.csv', 'resampled_22837.csv', 'resampled_22988.csv', 'resampled_22995.csv', 'resampled_23036.csv', 'resampled_23054.csv', 'resampled_23059.csv', 'resampled_23070.csv', 'resampled_23078.csv', 'resampled_23166.csv', 'resampled_23171.csv', 'resampled_23275.csv', 'resampled_23382.csv', 'resampled_23441.csv', 'resampled_23443.csv', 'resampled_23517.csv', 'resampled_23525.csv', 'resampled_23590.csv', 'resampled_23730.csv', 'resampled_23744.csv', 'resampled_23909.csv', 'resampled_23910.csv', 'resampled_23935.csv', 'resampled_23965.csv', 'resampled_23985.csv', 'resampled_24051.csv', 'resampled_24055.csv', 'resampled_24111.csv', 'resampled_24135.csv', 'resampled_24176.csv', 'resampled_24217.csv', 'resampled_24347.csv', 'resampled_24352.csv', 'resampled_24355.csv', 'resampled_24357.csv', 'resampled_24394.csv', 'resampled_24397.csv', 'resampled_24477.csv', 'resampled_24488.csv', 'resampled_24512.csv', 'resampled_24587.csv', 'resampled_24660.csv', 'resampled_24920.csv', 'resampled_25109.csv', 'resampled_25118.csv', 'resampled_25129.csv', 'resampled_25151.csv', 'resampled_25212.csv']

df = pd.read_csv("data/task-data/in-hospital-mortality/train_val_SMOTE_labels.csv")

df_filtered = df[~df['stay'].isin(Invalid_files)]
print(df.shape, df_filtered.shape)

df_filtered.to_csv("data/task-data/in-hospital-mortality/train_val_SMOTE_labels_validated.csv", index = False)

(25388, 2) (25222, 2)


# eICU

## Flat dataset

In [5]:
s = "train_0"

# Define paths
data_folder = 'data/task-data/in-hospital-mortality/eICU_dataset/train_0_filled_48H'
label_file = 'data/task-data/in-hospital-mortality/eICU_dataset/eICU_list_file_train_0.csv'
output_folder_labels = "data/task-data/in-hospital-mortality/eICU_dataset/"
 
# Load the labels
labels_df = pd.read_csv(label_file)
display(labels_df)

# Initialize lists to store data points and labels
data_list = []
label_list = []

counter = 1

# Iterate through each file and prepare data
for index, row in labels_df.iterrows():
    file_name = row['stay']
    label = row['y_true']  # Assuming the label column is named 'y_true'
    
    # Load the CSV file
    file_path = os.path.join(data_folder, file_name)
    df = pd.read_csv(file_path)

    df['Glascow coma scale eye opening'] = df['Glascow coma scale eye opening'].map(GCS_eye)
    df['Glascow coma scale motor response'] = df['Glascow coma scale motor response'].map(GCS_motor)
    df['Glascow coma scale verbal response'] = df['Glascow coma scale verbal response'].map(GCS_speech)
    df['Glascow coma scale total'] = df['Glascow coma scale total'].astype('Int64')
    df['Hours'] = df["Hours"].astype(float)
    
    # Flatten the 2D data into 1D
    data_flattened = df.values.flatten()
    
    # Add to the lists
    data_list.append(data_flattened)
    label_list.append(label)

    print(counter, file_name, label, df.shape, data_flattened.shape)
    counter += 1

# Convert to numpy arrays
X = np.array(data_list)
y = np.array(label_list)

print(X.shape, y.shape)

np.save(output_folder_labels + "X_" + s + "_filled_48H_flattened_raw.npy", X)
np.save(output_folder_labels + "y_" + s + "_filled_48H_flattened_raw.npy", y)


stay  y_true
0      2485759_episode1_timeseries.csv       0
1      1808361_episode1_timeseries.csv       0
2      1691711_episode1_timeseries.csv       0
3      1800387_episode1_timeseries.csv       0
4      1558650_episode1_timeseries.csv       0
...                                ...     ...
21471   970295_episode1_timeseries.csv       0
21472  1651646_episode1_timeseries.csv       0
21473  2266635_episode1_timeseries.csv       0
21474  1485000_episode1_timeseries.csv       0
21475  3155899_episode1_timeseries.csv       0

[21476 rows x 2 columns]

1 2485759_episode1_timeseries.csv 0 (49, 18) (882,)
2 1808361_episode1_timeseries.csv 0 (49, 18) (882,)
3 1691711_episode1_timeseries.csv 0 (49, 18) (882,)
4 1800387_episode1_timeseries.csv 0 (49, 18) (882,)
5 1558650_episode1_timeseries.csv 0 (49, 18) (882,)
6 3229585_episode1_timeseries.csv 0 (49, 18) (882,)
7 972694_episode1_timeseries.csv 0 (49, 18) (882,)
8 2215338_episode1_timeseries.csv 0 (49, 18) (882,)
9 3345321_episode1_timeseries.csv 0 (49, 18) (882,)
10 2497699_episode1_timeseries.csv 0 (49, 18) (882,)
11 3155246_episode1_timeseries.csv 0 (49, 18) (882,)
12 372004_episode1_timeseries.csv 0 (49, 18) (882,)
13 1243943_episode1_timeseries.csv 1 (49, 18) (882,)
14 169514_episode1_timeseries.csv 0 (49, 18) (882,)
15 360025_episode1_timeseries.csv 0 (49, 18) (882,)
16 1260536_episode1_timeseries.csv 0 (49, 18) (882,)
17 3218451_episode1_timeseries.csv 0 (49, 18) (882,)
18 2695709_episode1_timeseries.csv 0 (49, 18) (882,)
19 2206613_episode1_timeseries.csv 0 (49, 18) (882,)
20 286